In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import requests
import os

TELEGRAM_TOKEN = "8083975934:AAEFXz0ja40Z470mmZSqGej7g6p80Kt6wh0"  # o ponlo directamente como string
TELEGRAM_CHAT_ID = "1030345806"

def send_telegram_message(message):
    url = f"https://api.telegram.org/bot{TELEGRAM_TOKEN}/sendMessage"
    payload = {
        "chat_id": TELEGRAM_CHAT_ID,
        "text": message
    }
    try:
        response = requests.post(url, data=payload)
        if response.status_code != 200:
            print("❌ Error en la respuesta de Telegram:")
            print(response.status_code)
            print(response.text)
        else:
            print("✅ Mensaje enviado correctamente.")
    except Exception as e:
        print(f"❌ No se pudo enviar el mensaje de Telegram: {e}")


In [4]:
from financial.momentum.models.kerasAdvanced import KerasAdvancedModelFactory
from financial.momentum.experiment.modelExperiment import ModelExperimentFactory
import os
from dotenv import load_dotenv
from financial.momentum.utilities import find_dotenv
from financial.momentum.utilities import metrics
import financial.data as fd
from financial.io.file.cache import FileCache
import pandas as pd
from financial.lab.experiment import Experiment
from sklearn.metrics import r2_score
from financial.model import Model

import tensorflow as tf
from keras import backend as K
import gc

def reset_gpu():
    K.clear_session()
    tf.keras.backend.clear_session()
    gc.collect()

2025-07-21 20:53:20.058997: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-21 20:53:20.069012: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1753124000.080389 2073902 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1753124000.083783 2073902 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1753124000.093139 2073902 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking 

In [5]:
load_dotenv(dotenv_path=find_dotenv())

cache_path = os.environ["CACHE"]
model_path = os.environ["MODEL"]
print(model_path)
print(os.environ["DATA"])
datastore = fd.CachedDataStore(path=os.environ["DATA"], cache=FileCache(cache_path=cache_path+"/"))
print(datastore) 

/home/manidmt/TFG/OTRI/models/keras
/home/manidmt/TFG/OTRI/data
CachedDataStore with 960 data sources [cache stats: {'size': 0, 'hit': 0, 'miss': 0, 'write': 0, 'read': 0, 'update': 0}]


In [9]:
start_date = "1990-01-01"
end_date = "2025-06-30"
data = datastore.get_data("DX-Y.NYB", start_date, end_date)

In [6]:
import os
import pickle

def store_results(ticker: str, model_name: str, predictions: pd.Series):

    base_name = f"model-momentum-{model_name}-{ticker}"

    # Guardar .pkl para Wrapper
    with open(os.path.join(cache_path, base_name), "wb") as f:
        pickle.dump(predictions, f)
    print("Prediciones guardadas pickle")
    # Guardar .csv para inspección y web
    predictions.to_csv(os.path.join(model_path, model_name + "_preds.csv"))
    print("Prediciones guardadas csv")
    

In [7]:
factory = KerasAdvancedModelFactory()

In [8]:
from itertools import product

# Arquitecturas a probar
#architectures = ["cnn"]
architectures = ["rnn", "lstm", "cnn", "cnn2d", "transformer"]

# Hiperparámetros a explorar
layer_option = [64, 32]
activation = ["relu"]
batch_size = 32
epochs = 10

def ticker_single_models(ticker):

    data = datastore.get_data(ticker, start_date, end_date)    
    target = data[90 + 20:]
    
    for arch in architectures:
        name = f"{arch}_{ticker}_{end_date[:4]}_single"
        path = model_path + "/" + name

        try:
            if Model.from_file(name, path=os.environ["MODEL"]):
                print(f"Modelo {name} ya existe. Saltando...")
                send_telegram_message(f"Modelo {name} ya existe. Saltando...")
                continue
        except FileNotFoundError:
            print(f"📂 Modelo {name} no existe. Procediendo a entrenar...")
            send_telegram_message(f"Modelo {name} no existe. Procediendo a entrenar...")

        config = {
            "mode": "global",  
            "datastore": datastore,
            "ticker": ticker,
            "model_factory": factory,
            "name": name,
            "start_year": start_date,
            "end_year": end_date,
            "lookahead": 20,
            "horizon": 90,
            "model_params": {
                "architecture": arch,
                "topology": {
                    "layers": layer_option,
                    "activation": {
                        "hidden": activation,
                        "output": "linear"
                    }
                },
                "optimization": {
                    "optimizer": "adam",
                    "loss": "mean_squared_error",
                    "metrics": ["mae"],
                    "epochs": epochs,
                    "batch_size": batch_size,
                    "validation_split": 0.1
                }
            }
        }

        try:
            print("RUNNING MODEL:")
            experiment = ModelExperimentFactory.create_experiment(config)
            experiment.run()
            print("METRICS:")
            preds = experiment.reconstruct_absolute_predictions_from_relative()
            store_results(ticker, name, preds)
            send_telegram_message("Resultados guardados")
            metrics(experiment, preds, target, model_path)
            send_telegram_message("Metricas guardadas")
            reset_gpu()
        except Exception as e:
            print(f"Falló el modelo {name}: {e}")

In [9]:
ticker_single_models("GOOG")
ticker_single_models("BLK")
ticker_single_models("BAM")

I0000 00:00:1753112594.132565  389541 gpu_device.cc:2019] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 6132 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 4070 Laptop GPU, pci bus id: 0000:01:00.0, compute capability: 8.9


Modelo rnn_GOOG_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo lstm_GOOG_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
Modelo cnn_GOOG_2025_single ya existe. Saltando...


✅ Mensaje enviado correctamente.
Modelo cnn2d_GOOG_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo transformer_GOOG_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


...

✅ Mensaje enviado correctamente.
Modelo cnn2d_BLK_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo transformer_BLK_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo rnn_BAM_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
Modelo lstm_BAM_2025_single ya existe. Saltando...


✅ Mensaje enviado correctamente.
Modelo cnn_BAM_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo cnn2d_BAM_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
Modelo transformer_BAM_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


In [10]:
index_tickers = [
    "^GSPC",          # S&P 500
    "^IXIC",          # Nasdaq
    "^IBEX",          # Ibex 35
    "AMZN",
    "TSLA",
    "GOOG",
    "BAM",
    "BLK",
]

In [11]:

for ticker in index_tickers:
    ticker_single_models(ticker)

Modelo rnn_^GSPC_2025_single ya existe. Saltando...


✅ Mensaje enviado correctamente.
Modelo lstm_^GSPC_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo cnn_^GSPC_2025_single ya existe. Saltando...


✅ Mensaje enviado correctamente.
Modelo cnn2d_^GSPC_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo transformer_^GSPC_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


...

Modelo cnn_BAM_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
Modelo cnn2d_BAM_2025_single ya existe. Saltando...


✅ Mensaje enviado correctamente.
Modelo transformer_BAM_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo rnn_BLK_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
Modelo lstm_BLK_2025_single ya existe. Saltando...


✅ Mensaje enviado correctamente.
Modelo cnn_BLK_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.


Modelo cnn2d_BLK_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
Modelo transformer_BLK_2025_single ya existe. Saltando...
✅ Mensaje enviado correctamente.
